Threatened birds in NA: https://www.birds-of-north-america.net/Threatened_Birds.html

Extinct birds in NA: https://www.birds-of-north-america.net/extinct-birds-of-north-america.html

Perhaps it would be interesting to make a point about birds going extinct.

https://www.xeno-canto.org/ allows searching for specific birds, so getting my data should be fine!

---

While I think of an artistic point, I should get started with the autoencoding.

[Tim Sainburg](https://github.com/timsainb/AVGN) recommends GAIA and Variational Autoencoder for generative use.

VAE: https://blog.keras.io/building-autoencoders-in-keras.html

Sainburg's models (includes VAE, GAIA, +): https://github.com/timsainb/tensorflow2-generative-models

TensorFlow Convolutional VAE tutorial: https://www.tensorflow.org/tutorials/generative/cvae

Music Autoencoders: https://blog.goodaudience.com/using-tensorflow-autoencoders-with-music-f871a76122ba

In [1]:
import numpy as np
import glob
from pydub import AudioSegment
import scipy
import tensorflow as tf
import os

In [2]:
DATA_MP3 = "data/mp3/"
DATA_WAV = "data/wav/"
SESS = tf.Session()

In [3]:
def convert_mp3_to_wav(fp):
    
    mp3 = AudioSegment.from_mp3(fp)
    mp3.export(os.path.join("data/wav/", fp[:-4] + ".wav"), format="wav")

In [4]:
# convert_mp3_to_wav("piping-plover1.mp3")

In [5]:
import IPython

In [8]:
IPython.display.Audio("data/wav/piping-plover1.wav")

In [10]:
from scipy.fftpack import rfft, irfft

In [11]:
# wav_arr = []

# audio_binary = tf.read_file("piping-plover1.wav")

# wav_decoder = tf.audio.decode_wav(audio_binary, desired_channels=1)

# sample_rate, audio = SESS.run([wav_decoder.sample_rate, wav_decoder.audio])

In [12]:
# print(sample_rate)
# print(audio)

In [13]:
def get_batch(idx=0, batch_size=-1, sess=SESS):
    
    wav_arr = []
    
    ###
    #
    # TODO: Set up batches 
    #
    ###
    
    for fp in glob.glob(DATA_WAV + '*'):
        
        audio_binary = tf.read_file(fp)

        wav_decoder = tf.audio.decode_wav(audio_binary, desired_channels=1)

        sample_rate, audio = sess.run([wav_decoder.sample_rate, wav_decoder.audio])
        
        wav_arr.append(audio)
        
    return np.array(wav_arr), sample_rate

In [14]:
audio, sample_rate = get_batch()

In [15]:
audio.shape

(1, 881664, 1)

In [16]:
from functools import partial

In [18]:

LOSS_OUT_FILE = 'Epoch_Loss.txt'

# Learning rate
lr = 0.0001

# L2 regularization
l2 = 0.0001

input_size = 12348
hidden_1_size = 8400
hidden_2_size = 3440
hidden_3_size = 2800

# Change the epochs variable to define the 
# number of times we iterate through all our batches
epochs = 10

# Change the batch_size variable to define how many songs to load per batch
batch_size = -1

# Change the batches variable to change the number of batches you want per epoch
batches = 1

In [20]:
# Placeholder X, input size
X = tf.placeholder(tf.float32, shape=[None, input_size])
l2_regularizer = tf.keras.(l2)

AttributeError: module 'tensorflow._api.v1.layers' has no attribute 'l2_regularizer'

In [44]:

# Define our placeholder with shape [?, 12348]
X = tf.placeholder(tf.float32, shape=[None, inputs])
l2_regularizer = tf.contrib.layers.l2_regularizer(l2)

autoencoder_dnn = partial(tf.layers.dense, 
    activation=tf.nn.elu,
    kernel_initializer=tf.contrib.layers.variance_scaling_initializer(),
    kernel_regularizer=tf.contrib.layers.l2_regularizer(l2)
)

hidden_1 = autoencoder_dnn(X, hidden_1_size)
hidden_2 = autoencoder_dnn(hidden_1, hidden_2_size)
hidden_4 = autoencoder_dnn(hidden_2, hidden_3_size)
hidden_5 = autoencoder_dnn(hidden_4, hidden_2_size)
outputs =  autoencoder_dnn(hidden_5, inputs, activation=None)

reconstruction_loss = tf.reduce_mean(tf.square(outputs-X))
reg_loss = tf.get_collection(tf.GraphKeys.REGULARIZATION_LOSSES)
loss = tf.add_n([reconstruction_loss] + reg_loss)

optimizer = tf.train.AdamOptimizer(lr)
training_op = optimizer.minimize(loss)
init = tf.global_variables_initializer()

W1106 12:15:46.529422 140405583501120 deprecation.py:323] From <ipython-input-44-00d697c7779f>:11: dense (from tensorflow.python.layers.core) is deprecated and will be removed in a future version.
Instructions for updating:
Use keras.layers.dense instead.


In [46]:
with SESS as sess:
    init.run()
    
    for epoch in range(epochs):
        
        print("Epoch:", epoch)
        
        audio, sample_rate = get_batch(sess=sess)

In [ ]:
##### Run training
with tf.Session() as sess:
    init.run()
    
    for epoch in range(epochs):
        epoch_loss = []
        print("Epoch: " + str(epoch))
        for i in range(batches):
            ch1_song, ch2_song, sample_rate = next_batch(i, batch_size, sess)
            total_songs = np.hstack([ch1_song, ch2_song])
            batch_loss = []

            for j in range(len(total_songs)):
                x_batch = total_songs[j]
                _, l = sess.run([training_op, loss], feed_dict={X:x_batch})
                batch_loss.append(l)
                print("Song loss: " + str(l))

            print("Curr Epoch: " + str(epoch) + " Curr Batch: " + str(i) + "/"+ str(batches))
            print("Batch Loss: " + str(np.mean(batch_loss)))
            epoch_loss.append(np.mean(batch_loss))

        print("Epoch Avg Loss: " + str(np.mean(epoch_loss)))

        if epoch % 1000 == 0:
            ch1_song_new, ch2_song_new, sample_rate_new = next_batch(2, 1, sess)
            x_batch = np.hstack([ch1_song_new, ch2_song_new])[0]
            print("Sample rate: " + str(sample_rate_new))

            orig_song = []
            full_song = []
            evaluation = outputs.eval(feed_dict={X: x_batch})
            print("Output: " + str(evaluation))
            full_song.append(evaluation)
            orig_song.append(x_batch)

            # Merge the nested arrays
            orig_song = np.hstack(orig_song)
            full_song = np.hstack(full_song)

            # Compute and split the channels
            orig_song_ch1 = orig_song[:math.floor(len(orig_song)/2)]
            orig_song_ch2 = orig_song[math.floor(len(orig_song)/2):]
            full_song_ch1 = full_song[:math.floor(len(full_song)/2)]
            full_song_ch2 = full_song[math.floor(len(full_song)/2):]

            # Save both the untouched song and reconstructed song to the 'output' folder
            process_data.save_to_wav(full_song_ch1, full_song_ch2, sample_rate, orig_song_ch1, orig_song_ch2, epoch, 'output', sess)